<h2>Project Name: FLAUTO: Federated Learning with Automated
Dual-Level Hyperparameter Tuning  </h2>
<h3> Written by Rakib Ul Haque and supervised by Dr. Panos P. Markopoulos </h3>
<h4> Email: panagiotis.markopoulos@utsa.edu</h4>

<h1><b>Libraries</b></h1>

In [1]:
import pandas as pd
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision
import torchvision.transforms as transforms
import torchvision.models as models
from ultralytics import YOLO
import shutil
import os
from IPython.display import clear_output
import time
import pickle
import json
from IPython.display import clear_output
import copy
from collections import deque
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


<h1><b>Measures</b></h1>

In [2]:
# print function
def Print(string, dictionary):
    first_key = next(iter(dictionary))
    first_value = dictionary[first_key]
    print(f"{string}:{first_key}: {first_value[0][0]}\n")

# forbinus norm function
def forbinus_norm_function(w_i):
    value = 0
    for k in w_i.keys():
        value += torch.linalg.norm(w_i[k])
    return value.item()

# model deviation function
def model_deviation_function(m1, m2):
    
    #model deviation code
    w_i = {key: value.to(device) for key, value in m1.items()}
    w_f = {key: value.to(device) for key, value in m2.items()}
    
    model_deviation = 0
    for k in w_i.keys():
        model_deviation += torch.linalg.norm(w_f[k].to(torch.float) - w_i[k].to(torch.float)) / (torch.linalg.norm(w_i[k].to(torch.float) +1) )
    return model_deviation.item()


# data path identification
def on_train_epoch_end(trainer):
    """Custom logic for additional metrics logging at the end of each training epoch."""
    global path
    path=trainer.csv

# define function to add data from another DataFrame
def add_data_to_client(client_id, new_data):
    global clients
    if client_id in clients:
        # Append new data to the client's DataFrame
        clients[client_id] = pd.concat([clients[client_id], new_data], ignore_index=True)
    else:
        print(f"Client {client_id} does not exist.")


# deleting run folder for saving spaces
def delete_folder(folder_path):
    if os.path.exists(folder_path):
        # Remove the folder and all its contents
        shutil.rmtree(folder_path)
        print(f"Folder '{folder_path}' deleted successfully!")
    else:
        print(f"Folder '{folder_path}' does not exist.")



<h1><b>Train function</b></h1>

In [3]:
#averaging the weihgts

def average_weights_function(dicts):
    # Initialize an empty dictionary to store the summed weights
    summed_weights = {}
    
    # Initialize an empty dictionary to keep track of how many times each key is seen
    key_occurrences = {}
    
    # Iterate through all the dictionaries
    for d in dicts:
        for key, value in d.items():
            if key in summed_weights:
                summed_weights[key] += value
                key_occurrences[key] += 1
            else:
                summed_weights[key] = value
                key_occurrences[key] = 1
    
    # Create a dictionary to store the final averaged weights
    averaged_weights = {}
    
    # Iterate through the summed weights and divide by the number of occurrences for each key
    for key, value in summed_weights.items():
        if key_occurrences[key] > 1:
            averaged_weights[key] = value / key_occurrences[key]
        else:
            averaged_weights[key] = value  # If only present in one dict, keep as is
    
    return averaged_weights

In [4]:
def training( i_w, E, r, c, l_rate):

    print("\n\n\n=======current learning rate", l_rate, "====\n\n\n\n")
    #declear local model
    global path, count_e, client_limit, min_b, max_b, opti
    local_model=YOLO("initial_weights.pt").to(device)
    local_model.load_state_dict(i_w)
    print(local_model.info())
    total_val_loss=[]
    total_train_loss=[]
    c_limit=client_limit
    batch_s=min_b

    Step_Size_b=(max_b - batch_s) / (client_limit)
    
    rmd_pe=[]
    #rmd_pe.append(0)
    flag=0
    le_rate=l_rate
    #local_model.load_state_dict(i_w,strict=False)
    checking_weights = local_model.state_dict()
    Print(f"Client {c} functions weights", checking_weights)
    
    #epochs
    for e in range(0,E):
        count_e=count_e+1
        local_model.add_callback("on_train_epoch_end", on_train_epoch_end)
        local_model.train(data=f"{fl_a}/{set_up}/c{c}.yaml", project=f"{dst_folder}/train/round_{r}_client_{c}/{e}", 
                          workers=0, epochs=1, imgsz=512, 
                          split='train', lr0=le_rate, batch=batch_s, optimizer=opti, 
                          val=True, device=0)
        
        fff_weights = {k: v.clone() for k, v in local_model.state_dict().items()}
        
        modev_pe=model_deviation_function(i_w,fff_weights)
        rmd_pe.append(modev_pe)
        
        print("model deviation", modev_pe)
        
        #collecting results
        df = pd.read_csv(path)
        #print(path)
        #print(df)
        df.columns = df.columns.str.strip()
        
        t_loss= df['train/box_loss'] + df['train/cls_loss'] + df['train/dfl_loss']
        total_train_loss.append(t_loss.iloc[0])#print(df['train/box_loss'])
        
        v_loss= df['val/box_loss'] + df['val/cls_loss'] + df['val/dfl_loss']
        total_val_loss.append(v_loss.iloc[0])#print(df['train/box_loss'])

        

        if e>0:
            rmd_change=abs(rmd_pe[e]-rmd_pe[e-1])/rmd_pe[e-1]
            print("rmd_change", rmd_change)
            if( ((rmd_pe[e] <1) and (rmd_change*100) <20 ) or (total_train_loss[e] >= total_train_loss[e-1]) ):
                c_limit=c_limit-1
                if(c_limit<=0):
                    break
                batch_s= round(batch_s + Step_Size_b)
                if batch_s >= max_b:
                    batch_s = max_b
                
            
        #     print(abs(total_loss[e] - total_loss[e-1]))
        #     if abs(total_loss[e] - total_loss[e-1]) < 0.5:
        #         le_rate= le_rate * 0.5
        #         print(f"updated Lr {le_rate}")

        #         flag=flag+1
        #         if flag>=3:
        #             break
            
        # #add_data_to_client(f'client_{c}', df)
    
    #checking initial weights
    Print(f"Client {c} initial weights", i_w)
    #colleting final weights
    client_final_weights = {k: v.clone() for k, v in local_model.state_dict().items()}#local_model.state_dict()
    Print(f"Client {c} final weights",client_final_weights)    
    #clear_output(wait=False)
    #return client_final_weights, total_val_loss, v_loss.iloc[0]
    return client_final_weights, v_loss.iloc[0]

<h1><b>FL structure</b></h1>

In [5]:
def federated_learning(i_w, C, P, R, E, b_size):

    # declearning global validtion dictionary
    global global_model, min_LR, max_LR, global_Step_Size_LR, server_limit
    global validation_dict
    global dst_folder
    global device
    
    model_weights_queue = deque(maxlen=2)
    
    global_model.load_state_dict(i_w)
    c_lr=min_LR
    r_val_list=[]
    r_val_list.append(0)
    #global average_weights
    #loop for round
    for r in range(1,R+1):
        
        #global_model = YOLO("yolov8n-obb.yaml").load("current.pt").to(device)
        
        models=[]
        c_val_list=[]
        #global_model = YOLO(f"Fed_Avg/weights/round_{r-1}_weighs").to(device)
        i_w = {k: v.clone() for k, v in global_model.state_dict().items()}#global_model.state_dict()
        Print("Model's initial weights", i_w)
        # averaged training weights per rounds
        #average_weights = {}
        #loop for clients
        for c in range(1,C+1):

            #training
            clients_weight, val_loss=training(i_w, E, r, c, c_lr)
            models.append(clients_weight)
            c_val_list.append(val_loss)
        
        all_final_weights=average_weights_function(models)
        r_val_list.append( sum(c_val_list)/len(c_val_list) )

        model_weights_queue.append(all_final_weights)
        
        #torch.save(average_weights, f'{dst_folder}/weights/round_{r}_weighs.pt')
        os.makedirs(os.path.join(dst_folder, "weights"), exist_ok=True)  # Creates both Fed_Avg and weights if needed
        # Now you can save the weights as usual:
        torch.save(all_final_weights, f'{dst_folder}/weights/after_round_{r}_weighs.pt')


        # global_model = YOLO("initial_weights.pt").to(device)
        # global_model.load_state_dict(average_weights)
        val_model = YOLO("initial_weights.pt").to(device)
        val_model.load_state_dict(all_final_weights)
        #global_model = load_model_weights_partial("yolov8n-obb.yaml", average_weights, device)
             
        #chceking averaged weights
        c_weight= {k: v.clone() for k, v in global_model.state_dict().items()}#global_model.state_dict()
        Print(f"updated global model after round {r}",c_weight)
        
        #performing round validations
        validation_results = val_model.val(data=f"{fl_a}/c5.yaml", project=f"{dst_folder}/val/round_{r}", 
                                           imgsz=512, batch=4, split='val', device=0, workers=0)
        
        #save validation results into dict 
        validation_dict[f"round_{r}"] = validation_results

        if r>1:
            if server_limit > 0:
                #round_LR_context.append( (iid_val_loss[i] > iid_val_loss[i-1]) and (min_LR > 0.0001) )
                if (r_val_list[r] > r_val_list[r-1]) and (min_LR > 0.0001):
                    max_LR=min_LR
                    min_LR=round(min_LR - global_Step_Size_LR,4)
                    min_LR=min_LR
                    server_limit=server_limit-1
                    global_Step_Size_LR = (max_LR - min_LR) / (2 ** server_limit)
                    all_final_weights = model_weights_queue.popleft()
                    model_weights_queue.clear()
                    model_weights_queue.append(all_final_weights)
                    #c_lr=min_LR
                elif r_val_list[r] <= r_val_list[r-1]:
                    min_LR=round(min_LR + global_Step_Size_LR,4)
                    if min_LR>=max_LR:
                        min_LR=max_LR
                c_lr=min_LR
                        
        global_model = YOLO("initial_weights.pt").to(device)
        global_model.load_state_dict(all_final_weights)

        #chceking averaged weights
        c_weight= {k: v.clone() for k, v in global_model.state_dict().items()}#global_model.state_dict()
        Print(f"updated global model after round {r}",c_weight)
        
        #Print("updated global model",i_w)
        
        print("round", r, "completed")
        # clear_output(wait=False)

<h1><b>Define Parameters</b></h1>

In [6]:
# fl_a="hFL"
# set_up="IID"
# dst_folder = f"{fl_a}_Fed_Avg"
# print(dst_folder)

In [7]:
#===========================Parameters==============================================================
round_no=30
client_no=4
participating_client=client_no
# learning_rate=0.01
batch_size=4
epochs=5
opti='Adam'
count_e=0


min_LR=0.0001
min_b=4
max_LR=0.09
max_b=6


client_limit=4 #4 is used to generate all the graphs 
server_limit=4 #4 is sued to generate al the graphs


global_Step_Size_LR = (max_LR - min_LR) / (( 2 ** server_limit))

# momentum=0.937
# weight_decay=0.0005

#=====================result variables===============================================================
# iid_model_deviation=[]
# iid_model_deviation.append(0)

#===========other variables=============================================
validation_dict = {}
# Define the destination folder

# ===========================================FL type
# fl_a="vFL"
fl_a="hFL"

# ===========================================FL data setup applicable for cleint 4
# set_up="IID"
# set_up="limited_epoch"
set_up="limited_data"
# set_up="miss_labeling"
# set_up="salt_papper"
forname=set_up

dst_folder = f"{fl_a}_{forname}_Fed_AutoHT_{opti}"
# dst_folder = f"Fed_Avg"
delete_folder(dst_folder)


path=""

#client results storage
clients = {f'client_{i}': pd.DataFrame(columns=['epoch', 'train/box_loss', 'train/cls_loss', 'train/dfl_loss',
       'metrics/precision(B)', 'metrics/recall(B)', 'metrics/mAP50(B)',
       'metrics/mAP50-95(B)', 'val/box_loss', 'val/cls_loss', 'val/dfl_loss',
       'lr/pg0', 'lr/pg1', 'lr/pg2']) for i in range(1,10)}



#===================================loading the saved weight list====================================================
global_model = YOLO("initial_weights.pt").to(device)
global_model.info()
initial_weights = {k: v.clone() for k, v in global_model.state_dict().items()}#global_model.state_dict()
print(len(initial_weights))
Print("Model's initial weights", initial_weights)
# global_model.save('current.pt')

Folder 'hFL_limited_data_Fed_AutoHT_Adam' does not exist.
YOLO11n-obb summary: 344 layers, 2,662,287 parameters, 0 gradients, 6.7 GFLOPs
541
Model's initial weights:model.model.0.conv.weight: tensor([[-0.0955, -0.4358, -0.4158],
        [-0.3618, -0.8042, -0.8950],
        [-0.3513, -0.8271, -0.8511]], device='cuda:0')



<h1><b>Round 0</b></h1>

In [8]:
l_model = YOLO("initial_weights.pt").to(device)
#server validation rounds
validation_results = l_model.val(data=f"{fl_a}/c5.yaml", project=f"{dst_folder}/val/round_0", imgsz=512, batch=4,split='val', device=0,workers=0)
validation_dict["round_0"] = validation_results
print(validation_results)

#=================================================================client_1====================
l_model = YOLO("initial_weights.pt").to(device)
l_model.val(data=f"{fl_a}/{set_up}/c1.yaml", project=f"{dst_folder}/train/round_0_client_1", imgsz=512, batch=4, split='train', device=0, workers=0)

#=================================================================client_2====================
l_model = YOLO("initial_weights.pt").to(device)
l_model.val(data=f"{fl_a}/{set_up}/c2.yaml", project=f"{dst_folder}/train/round_0_client_2", imgsz=512, batch=4, split='train', device=0, workers=0)


#=================================================================client_3====================
l_model = YOLO("initial_weights.pt").to(device)
l_model.val(data=f"{fl_a}/{set_up}/c3.yaml", project=f"{dst_folder}/train/round_0_client_3", imgsz=512, batch=4, split='train',device=0, workers=0)


#=================================================================client_4====================
l_model = YOLO("initial_weights.pt").to(device)
l_model.val(data=f"{fl_a}/{set_up}/c4.yaml", project=f"{dst_folder}/train/round_0_client_4", imgsz=512, batch=4, split='train', device=0, workers=0)
clear_output(wait=False)

<h1><b>Run FL</b></h1>

In [9]:
#parameters 3,085,440 parameters, 3,085,424 gradients
federated_learning(initial_weights, client_no, participating_client, round_no, epochs, batch_size)

Model's initial weights:model.model.0.conv.weight: tensor([[-0.0955, -0.4358, -0.4158],
        [-0.3618, -0.8042, -0.8950],
        [-0.3513, -0.8271, -0.8511]], device='cuda:0')




=======current learning rate 0.0001 ====




YOLO11n-obb summary: 344 layers, 2,662,287 parameters, 0 gradients, 6.7 GFLOPs
(344, 2662287, 0, 6.6913920000000005)
Client 1 functions weights:model.model.0.conv.weight: tensor([[-0.0955, -0.4358, -0.4158],
        [-0.3618, -0.8042, -0.8950],
        [-0.3513, -0.8271, -0.8511]], device='cuda:0')

New https://pypi.org/project/ultralytics/8.3.53 available 😃 Update with 'pip install -U ultralytics'
Ultralytics 8.3.49 🚀 Python-3.12.4 torch-2.4.0 CUDA:0 (NVIDIA RTX A6000, 48670MiB)
engine/trainer: task=obb, mode=train, model=initial_weights.pt, data=hFL/limited_data/c1.yaml, epochs=1, time=None, patience=100, batch=4, imgsz=512, save=True, save_period=-1, cache=False, device=0, workers=0, project=hFL_limited_data_Fed_AutoHT_Adam/train/round_1_client_1/0, name=tra

train: Scanning /home/RAKIB/Paper_1_Codes/paper_2/yolov11n_dotav2.0/hFL_clients_data/limited_data/client_1/train/labels.cache... 70 images, 0 backgrounds, 0 corrupt: 100%|██████████| 70/70 [00:00<?, ?it/s]
val: Scanning /home/RAKIB/Paper_1_Codes/paper_2/yolov11n_dotav2.0/hFL_clients_data/limited_data/client_1/val/labels.cache... 50 images, 0 backgrounds, 0 corrupt: 100%|██████████| 50/50 [00:00<?, ?it/s]

Plotting labels to hFL_limited_data_Fed_AutoHT_Adam/train/round_1_client_1/0/train/labels.jpg... 


optimizer: Adam(lr=0.0001, momentum=0.937) with parameter groups 87 weight(decay=0.0), 97 weight(decay=0.0005), 96 bias(decay=0.0)
Image sizes 512 train, 512 val
Using 0 dataloader workers
Logging results to hFL_limited_data_Fed_AutoHT_Adam/train/round_1_client_1/0/train
Starting training for 1 epochs...

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


        1/1       5.7G      1.801      2.048      1.816         66        512: 100%|██████████| 18/18 [00:03<00:00,  5.43it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 13/13 [00:05<00:00,  2.38it/s]


...

                   all         15        361      0.631      0.388      0.446      0.263

1 epochs completed in 0.001 hours.
Optimizer stripped from hFL_limited_data_Fed_AutoHT_Adam/train/round_30_client_4/4/train/weights/last.pt, 5.6MB
Optimizer stripped from hFL_limited_data_Fed_AutoHT_Adam/train/round_30_client_4/4/train/weights/best.pt, 5.6MB

Validating hFL_limited_data_Fed_AutoHT_Adam/train/round_30_client_4/4/train/weights/best.pt...
Ultralytics 8.3.49 🚀 Python-3.12.4 torch-2.4.0 CUDA:0 (NVIDIA RTX A6000, 48670MiB)
YOLO11n-obb summary (fused): 257 layers, 2,654,503 parameters, 0 gradients, 6.6 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 4/4 [00:00<00:00,  4.04it/s]


                   all         15        361       0.63       0.38      0.446      0.263
                harbor          8        127       0.71      0.539       0.55      0.266
                 plane          5        217       0.93      0.616      0.852      0.578
         swimming-pool          2          5      0.728        0.2      0.253       0.11
          tennis-court          2         12      0.152      0.167      0.128     0.0956
Speed: 0.2ms preprocess, 4.8ms inference, 0.0ms loss, 3.4ms postprocess per image
Results saved to hFL_limited_data_Fed_AutoHT_Adam/train/round_30_client_4/4/train
model deviation 21.769453048706055
rmd_change 0.11253129446094377
Client 4 initial weights:model.model.0.conv.weight: tensor([[-0.0952, -0.4370, -0.4231],
        [-0.3622, -0.8109, -0.8918],
        [-0.3524, -0.8279, -0.8607]], device='cuda:0')

Client 4 final weights:model.model.0.conv.weight: tensor([[-0.0953, -0.4365, -0.4226],
        [-0.3630, -0.8110, -0.8931],
        [-0.3530, -

val: Scanning /home/RAKIB/Paper_1_Codes/paper_2/yolov11n_dotav2.0/hFL_clients_data/client_5/val/labels.cache... 50 images, 0 backgrounds, 0 corrupt: 100%|██████████| 50/50 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 13/13 [00:01<00:00,  8.51it/s]


                   all         50       1063      0.836      0.798      0.863      0.604
                harbor         20        493      0.767      0.783      0.812       0.47
                 plane          8        205      0.845      0.854      0.912      0.675
         swimming-pool         15        228      0.862      0.614       0.76      0.375
          tennis-court         20        137      0.872      0.942      0.967      0.898
Speed: 0.2ms preprocess, 4.0ms inference, 0.0ms loss, 2.2ms postprocess per image
Results saved to hFL_limited_data_Fed_AutoHT_Adam/val/round_30/val
updated global model after round 30:model.model.0.conv.weight: tensor([[-0.0961, -0.4370, -0.4242],
        [-0.3624, -0.8104, -0.8925],
        [-0.3524, -0.8274, -0.8607]], device='cuda:0')

round 30 completed


In [10]:
print("global epoch", count_e)

global epoch 600


<h1><b>Save the validation dict</b></h1>

In [11]:
# Convert the dict to a serializable format
def dict_to_serializable(d):
    serializable_dict = {}
    for key, value in d.items():
        if isinstance(value, (int, float, str, list, dict)):
            serializable_dict[key] = value
        else:
            serializable_dict[key] = str(value)  # Convert non-serializable types to string
    return serializable_dict

# Save as JSON
save_dir = dst_folder
os.makedirs(save_dir, exist_ok=True)
file_path = os.path.join(save_dir, 'validation_dict.json')

with open(file_path, 'w') as f:
    json.dump(dict_to_serializable(validation_dict), f, indent=4)

print(f"Validation dictionary saved to {file_path}")


Validation dictionary saved to hFL_limited_data_Fed_AutoHT_Adam/validation_dict.json


In [12]:
file_path = os.path.join(save_dir, 'validation_dict.json')

# Load the JSON file
with open(file_path, 'r') as f:
    loaded_dict = json.load(f)

# Print the loaded dictionary
print("Validation dictionary loaded successfully")


Validation dictionary loaded successfully


In [13]:
validation_dict['round_1']

ultralytics.utils.metrics.OBBMetrics object with attributes:

ap_class_index: array([0, 1, 2, 3])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x74e4cc285430>
curves: []
curves_results: []
fitness: 0.4284951686713902
keys: ['metrics/precision(B)', 'metrics/recall(B)', 'metrics/mAP50(B)', 'metrics/mAP50-95(B)']
maps: array([    0.21463,     0.54383,     0.17897,     0.67401])
names: {0: 'harbor', 1: 'plane', 2: 'swimming-pool', 3: 'tennis-court'}
plot: True
results_dict: {'metrics/precision(B)': 0.762736172275112, 'metrics/recall(B)': 0.5673716572993529, 'metrics/mAP50(B)': 0.6592096450566013, 'metrics/mAP50-95(B)': 0.40286022685081113, 'fitness': 0.4284951686713902}
save_dir: PosixPath('hFL_limited_data_Fed_AutoHT_Adam/val/round_1/val')
speed: {'preprocess': 0.13765335083007812, 'inference': 15.605549812316895, 'loss': 0.00133514404296875, 'postprocess': 9.886026382446289}

In [14]:
validation_dict['round_30']

ultralytics.utils.metrics.OBBMetrics object with attributes:

ap_class_index: array([0, 1, 2, 3])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x74e4cc18c8f0>
curves: []
curves_results: []
fitness: 0.6300168210724397
keys: ['metrics/precision(B)', 'metrics/recall(B)', 'metrics/mAP50(B)', 'metrics/mAP50-95(B)']
maps: array([    0.46972,     0.67454,     0.37481,     0.89765])
names: {0: 'harbor', 1: 'plane', 2: 'swimming-pool', 3: 'tennis-court'}
plot: True
results_dict: {'metrics/precision(B)': 0.8363571525514414, 'metrics/recall(B)': 0.7980652310417425, 'metrics/mAP50(B)': 0.8625564852755758, 'metrics/mAP50-95(B)': 0.6041790806054246, 'fitness': 0.6300168210724397}
save_dir: PosixPath('hFL_limited_data_Fed_AutoHT_Adam/val/round_30/val')
speed: {'preprocess': 0.19323348999023438, 'inference': 3.9769792556762695, 'loss': 0.0016450881958007812, 'postprocess': 2.1990203857421875}

In [15]:
len(validation_dict)

31